# Feature Selection using the Adjusted Mutual Information (AMI) Score 

### (DNS analysis only)

This notebook uses the Adjusted Mutual Information Score to determine the most relevant features in the DDoS attacks. It uses the bigflows pcap from [http://tcpreplay.appneta.com/wiki/captures.html] containing normal network traffic. The DDoS attack pcaps from DDoSDB [https://ddosdb.org/] are used to compare it with the normal network traffic.

In [1]:
#all relevant libraries need to be imported
from sklearn.metrics.cluster import adjusted_mutual_info_score, mutual_info_score, normalized_mutual_info_score
from sklearn.feature_selection import mutual_info_classif
import numpy as np
import dpkt
import Utils
import ipaddress
import pandas as pd
import time
import os
import json
import operator
import sys
# import dnslib
# from dns_packet import *
# from kaitaistruct import KaitaiStream, BytesIO
from scapy.all import *
from scapy.layers.dns import DNS, DNSQR
import logging
logging.getLogger("scapy.runtime").setLevel(logging.ERROR)

### Load bigflows containing only UDP traffic

In [ ]:
start = time.time()

input = open('normal_pcaps/bigflows_dns.pcap', 'rb')
normal = dpkt.pcap.Reader(input)
length = 4372 #this is the number of packets in bigflows_udp.pcap   #791615 #791179

ips_n = np.empty(length)
protocol_n = np.empty(length)
total_length_n = np.empty(length)
src_port_n = np.empty(length)
dst_port_n = np.empty(length)
udp_length_n = np.empty(length)

dns_opcode_n = np.empty(length)
dns_answerlength_n = np.empty(length)
dns_questionlength_n = np.empty(length)
dns_additional_recordlength_n = np.empty(length)
dns_RRlength_n = np.empty(length)

dns_flag_response_n = np.empty(length)
dns_flag_truncated_n = np.empty(length)
dns_flag_authorative_n = np.empty(length)
dns_flag_recursiond_n = np.empty(length)
dns_flag_recursiona_n = np.empty(length)

dns_reply_code_n = np.empty(length)

dns_answer_type_n = np.empty(length)
dns_answer_class_n = np.empty(length)
dns_answer_name_n = np.empty(length)
dns_answer_size_n = np.empty(length)

dns_question_name_n = np.empty(length)
dns_question_class_n = np.empty(length)
dns_question_type_n = np.empty(length)

labels_n = np.zeros(length)

udp_packet = 0
tcp_packet = 0
dns_packet = 0
other = 0
total_packet = 0
 
    
printb = 0
i=0
for ts, buf in normal:
#     eth = dpkt.ethernet.Ethernet(buf)
    pkt = scapy.layers.l2.Ether(buf)

    total_packet += 1 

    if pkt.haslayer(IP):
        ip = pkt['IP']
#         ip = eth.data
        ips_n[i] = Utils.ip_to_uint32(ip.src)
        protocol_n[i] = ip.proto
        total_length_n[i] = ip.len
        
        if ip.proto == 6:
            tcp_packet += 1
#             TCP=ip.data
            tcp = pkt['TCP']
            dst_port_n[i] = tcp.dport
            src_port_n[i] = TCP.sport
        elif ip.proto == 17:
            udp_packet += 1
            udp = pkt['UDP']
            if pkt.haslayer(DNS):
                dns = pkt['DNS']
                dns_packet += 1
                
#                 dns = scapy.layers.dns.DNS(UDP.data)

                dns_opcode_n[i] =  dns.opcode
                dns_answerlength_n[i] = dns.ancount
                dns_questionlength_n[i] = dns.qdcount
                dns_additional_recordlength_n[i] = dns.arcount
                dns_RRlength_n[i] = dns.nscount
                
                dns_flag_response_n[i] = dns.qr
                dns_flag_truncated_n[i] = dns.tc
                dns_flag_authorative_n[i] = dns.aa #authorative answer
                dns_flag_recursiond_n[i] = dns.rd
                dns_flag_recursiona_n[i] = dns.ra
                
                dns_reply_code_n[i] = dns.rcode
                
                if (isinstance(dns.an, DNSRR)):
                    dns_answer_type_n[i] = dns.an.type
                    dns_answer_name_n[i] = int.from_bytes(dns.an.rrname, "little")
                    dns_answer_class_n[i] = dns.an.rclass
                    dns_answerlength_n[i] = dns.an.rdlen
                else:
                    dns_answer_type_n[i] = -1
                    dns_answer_name_n[i] = -1
                    dns_answer_class_n[i] = -1
                    dns_answer_size_n[i] = -1
                
                if (isinstance(dns.qd, DNSQR)):
                    dns_question_class_n[i] = dns.qd.qclass
                    dns_question_name_n[i] = int.from_bytes(dns.qd.qname, "little")
                    dns_question_type_n[i] = dns.qd.qtype
                else:
                    dns_question_class_n[i] = -1
                    dns_question_name_n[i] = -1
                    dns_question_type_n[i] = -1
                    
                    
                dst_port_n[i] = udp.dport
                src_port_n[i] = udp.sport
                udp_length_n[i] = udp.len
            else:
                other +=1
                
        else:
            other += 1
            dst_port_n[i] = 0
            src_port_n[i] = 0
    else:
        other += 1
        
    i += 1

input.close()
print("total # of packets: %s"  % (total_packet))
print("# of UDP packets: %s" % (udp_packet))
print("# of TCP packets: %s" % (tcp_packet))
print("# of DNS packets: %s" % (dns_packet))
print("# of other packets except for TCP or UDP: %s"  % (other))

end = time.time()
print(end - start)


In [49]:
input = open('attack_pcaps/07618097a64126cfe87e099b3054a073.pcap', 'rb')
# input = open('attack_pcaps/41fd4b0156a33263722ee03c74e238a4.pcap', 'rb')
normal = dpkt.pcap.Reader(input)
check = 0
counter = 0

# pcap = 'attack_pcaps/41fd4b0156a33263722ee03c74e238a4.pcap'
# pkts = rdpcap(pcap)

# print(type(pkts[0]))
print("start")
for ts, buf in normal:

    pkt = scapy.layers.l2.Ether(buf + b'\x01\x01\x00\x02')
    
#     dns = pkt['DNS']
    check += 1
    print("#", check)
    if pkt.haslayer(IP):
        ip = pkt['IP']
        if ip.proto == 6:
            tcp = pkt['TCP']
        elif ip.proto == 17:
            udp = pkt['UDP']
#             payload = 'ZZZZZZZZZZZZZZZZZZZZZ'
#             pkt = pkt / payload
            print(pkt['Raw'])
#             if not pkt.haslayer(DNS):
# #                 dns = scapy.layers.dns.DNS(buf + b'\x01\x01\x00\x02\x01\x01\x00\x02')#, '\x01\x01\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00\x00\x02\x00\x04\x00\x00\x00')#\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00')#\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00')# + b'\x01\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00')#\x00\x02\x00\x03\x00\x00\x00\x04\x00\x00\x00')
#                 print(dns.rd.)
            
#     ip = pkt['IP']
#     udp = pkt['UDP']
#     dns = pkt['DNS']
        
#         print("#", check)
# #         dd = UDP.data
#         print(UDP.ulen)
# #         if(UDP.ulen > 1800):
# #             continue
#         try:
#             if buf.haslayer(DNS):
#                 dns = scapy.layers.dns.DNS(dd)
#         except:
#             dns = scapy.layers.dns.DNS(dd)
            
print(counter)

start
# 1
b'm\x0c\x81\x80\x00\x01\x00\x1d\x00\x06\x00\x00\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x00\x06\x00\x01\x00\x00\x1a\x0e\x00:\x03ns1\xc0\x0c\x1dit.aciouns.external.dns.admin\xc0\x0cw\xcfu\x0e\x00\x00*0\x00\x00\x0e\x10\x00$\xea\x00\x00\x00\x03\x84\xc0\x0c\x00.\x00\x01\x00\x00\x1a\x0e\x00\x9b\x00\x06\x07\x02\x00\x00\x1c T\xa4\xb8]T\x9bo\xcdt!\x03irs\x03gov\x00\x80\x9d\x9b\xce\xbe~\x93\xc5eL\x8b\xc6\x99\xf72U?\x92Y\xf2!O\x1d\x95^\xdf\xa5\xea2\x1boK,\x1c`,\xa3-\xe3\xe4\x03$\x05s0e\xceQ\xc2\xdc0|\x92\xa7\xb3\x19nn\xcef\xb21\x90u"\x80Gj\xfb\x08\x08\xa4=Ge\xc7"\n\xd0\xcb\xb3\xe2\xb2\x1f_\xe6\x18\x15\xa0\x1c!\xd5]ri\x01\x0fw\x8f.\xd31\xd2r\x9c\xfd\xe3\xf4W\x12\x9e\x81\xa6;{\xa2\xae"k\x86(\xea\xc16\xbb\xfb\xa5\x11\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1a\x0e\x00\t\x00\n\x04emg1\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1a\x0e\x00\t\x00\n\x04emg2\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1a\x0e\x00\t\x00\n\x04emg3\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1a\x0e\x00\t\x00\n\x04emg4\xc0\x0c\xc

# 92
b't\x87\x81\x80\x00\x01\x00\x1d\x00\x00\x00\x07\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1bx\x00\t\x00\n\x04emg1\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1bx\x00\t\x00\n\x04emg2\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1bx\x00\t\x00\n\x04emg3\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1bx\x00\t\x00\n\x04emg4\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1bx\x00\t\x00\n\x04emg5\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1bx\x00\t\x00\n\x04emg6\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1bx\x00\t\x00\x14\x04emgw\xc0\x0c\xc0\x0c\x00.\x00\x01\x00\x00\x1bx\x00\x9b\x00\x0f\x07\x02\x00\x00\x1c T\xa4\xb8]T\x9bo\xcdt!\x03irs\x03gov\x00\x9e\x11B\xc0\xe4\xb5np9O\x155f\xaf\x99{\xbf\xb6$\xd1\x9b\x14\xd8\n\xf0\xd7\xc0\x0f\xe3\xe7]Z\xaab\x99y\x08\x02\xcc,\xdb\xb9-\x7f,\xdc\x17\xb5\xf1\x9e\x0bA\x0c\x05w\xe4\xb1\xea\x80E\x95(5\xc0T\xb0\xbe\x7f\xbe\x18I\xf7qe0\xd4 \xe3dt\x82hY\x83\xd5\x9d\xc3V\x9c\x94\xfc\xd7\xb1C\xe2\xb8\xe4\xa3\xd3\x1ck\xda\xde\xbe\xa6\x06\xafG\x15\x87\xb3\x82\xaf\

# 211
b'ko\x81\x80\x00\x01\x00\x1d\x00\x00\x00\x07\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x00\x0f\x00\x01\x00\x00\x18[\x00\t\x00\n\x04emg1\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x18[\x00\t\x00\n\x04emg2\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x18[\x00\t\x00\n\x04emg3\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x18[\x00\t\x00\n\x04emg4\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x18[\x00\t\x00\n\x04emg5\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x18[\x00\t\x00\n\x04emg6\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x18[\x00\t\x00\x14\x04emgw\xc0\x0c\xc0\x0c\x00.\x00\x01\x00\x00\x18[\x00\x9b\x00\x0f\x07\x02\x00\x00\x1c T\xa3f\xdeT\x9a\x1eNt!\x03irs\x03gov\x00w\xa0\xac?\x03+\x98\xe3\x19g\x90\xab\xfd\xc0\xf0{\xb1f\xbdp\xf7T6\xd9Lz\xce\xce\xed<\xcd\x91^<\x12A\xf0\xebaS/\x00\xe2\xca\xcd\xba\x92\x98\x93\x84\x02\x83\xbeY.\x881\x1d0\xbf%\xc9\xb9\xd7OE\xb5\xbd\xa9\x988L\xd4\xbb\x1a\xce\x0b\x1b\xd0g\x032$\r\\\tG\xa2\xf8\x05\x08m\xe4"\xf2\xe5\xe8\x88=\x13G\x85RG\xb61\xa0\xde+#\xa3KR\xde\xb0\xb3\xb3\xe9\xa8qDr\

# 264
b't\x87\x81\x80\x00\x01\x00\x1d\x00\x00\x00\r\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x00\x01\x00\x01\x00\x00\x01\xc9\x00\x04\xa6{\xda\xdc\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x91\x00\x06\x03ns1\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x91\x00\x06\x03ns2\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x91\x00\x06\x03ns3\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x91\x00\x06\x03ns4\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x91\x00\x06\x03ns5\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x91\x00\x06\x03ns6\xc0\x0c\xc0\x0c\x00\x06\x00\x01\x00\x00\x1b\x91\x006\xc05\x1dit.aciouns.external.dns.admin\xc0\x0cw\xcfu\r\x00\x00*0\x00\x00\x0e\x10\x00$\xea\x00\x00\x00\x03\x84\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x91\x00\t\x00\n\x04emg1\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x91\x00\t\x00\n\x04emg2\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x91\x00\t\x00\n\x04emg3\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x91\x00\t\x00\n\x04emg4\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x91\x00\t\x00

# 335
b'ko\x81\x80\x00\x01\x00\x19\x00\x06\x00\x00\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x003\x00\x01\x00\x00\x15\xdb\x00\t\x01\x00\x00d\x04\xaa\xbb\xcc\xdd\xc0\x0c\x00.\x00\x01\x00\x00\x15\xdb\x00\x9b\x003\x07\x02\x00\x00\x1c T\xa4\xb8]T\x9bo\xcdt!\x03irs\x03gov\x00\x1f\xf8Xk}C/\xc0\x05r\xf8\xb3\x80\x98<\xc9\x8at\xae<w\x08\xefU(U\xbc\x00\xcf\x07y\xdf\xcc\xe8m\x07\xf3\xaa\x03e\xb0\x08\x89C\x1e&\xd0\xaa\x03Q\xee\x17\x86\x0bi\\1a\xb4\xca\xfe_\xc2\xf559\xf0\x10\xf9\xf6\x00\xb27D\x19\x80\xceg\xda\x02\xdb\xddz\xf9\x1e\xb1\xb2f20\xab\x921]\xf0:\xe6\xcc\x91\xfa\xd7hPR\x8d\xcb\xc2]^x\xedK\xc7wx\x88\xb7N(E\xe5)[\xb3o\xf4\xfaT\xc0\x0c\x000\x00\x01\x00\x00\x15\xdb\x00\x88\x01\x00\x03\x07\x03\x01\x00\x01\xb2\xc2\xba\xe3\xde\x86\x06\xcaR\\\x12%\xa2\x1f\xd7\x98\r\xc5\x16\xdd\t6\xfe\x9b\xf5:g\xd2j\x1c\x05\xadB\x06\x9e\xf1w\x839\x9dN\x1d\x83\xdc0\x04)\x90\x8ak\x84v\xda}\xf8\xa1@\x08\xd0?\xdcj\xb1\x892\x17\x00\xac\xcb\x05wd\xb9)\xc5\x95=\r\xddI\xb4\xa0\x96w\xf0\xb0\xe6Pt\x0c\xf1}^\xcc\x9d\xb1fvw\xf

...

# 726
b't\x87\x81\x80\x00\x01\x00\x1d\x00\x00\x00\r\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x00\x01\x00\x01\x00\x00\x01\xc8\x00\x04\xa6{\xda\xdc\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x90\x00\x06\x03ns1\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x90\x00\x06\x03ns2\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x90\x00\x06\x03ns3\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x90\x00\x06\x03ns4\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x90\x00\x06\x03ns5\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x1b\x90\x00\x06\x03ns6\xc0\x0c\xc0\x0c\x00\x06\x00\x01\x00\x00\x1b\x90\x006\xc05\x1dit.aciouns.external.dns.admin\xc0\x0cw\xcfu\r\x00\x00*0\x00\x00\x0e\x10\x00$\xea\x00\x00\x00\x03\x84\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x90\x00\t\x00\n\x04emg1\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x90\x00\t\x00\n\x04emg2\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x90\x00\t\x00\n\x04emg3\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x90\x00\t\x00\n\x04emg4\xc0\x0c\xc0\x0c\x00\x0f\x00\x01\x00\x00\x1b\x90\x00\t\x00

# 795
b't\x87\x81\x80\x00\x01\x00\x19\x00\x06\x00\x00\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x00.\x00\x01\x00\x00\x15\xdb\x01\x1b\x000\x07\x02\x00\x00\x1c T\xa4\xb8]T\x9bo\xcd\x03v\x03irs\x03gov\x00THm\x19\xd7wUG\xcc4\xbb\x96\x90\xb0\x19\x80\xec\xf3J\xd5\x81M\xad\xb6vs\x077\x0e\x97d\xf8<#\xe9\xdb\xc3\x02\x14\xba\xeb\x94\xef\xfc\x14"7\xa1\xf4Q\npj\x88\xaa\xd0\xab\x01\xa8F\x1f\xe8\xe6\xd6\xa7,\xaeY\xe5en\xc3\x87U\xc1/\x9e`G\xf1j\xdfm\xc43[\xdeg\x16\x1d\xfb\xbdW\xaeF\x01\xed\xdeFh[c*\x13\x90\'\x94\xc4AP\xfdS\xa6`\xfe\xfejkB\xe7\xfc\xa40\xd0\xc3<\xcbscevM\xbd\xea\xb8\x94\xdc\x9at\xe1\ts3\xb0\xbcc\xfd*\x15\xbc\xa5D\xb2\xf7\xbc9\x88\xaf\x14YN\x9c;\x1b\x86tfj\x88\x8a\x15\\\xfb\xadUI\x859\xa1!\xfb&\xae7\xe1\xfd\xc9\x1e\x0f\'\xd0(x\xda\xfaj\x16\xb8onhQ\x03\x93\xed\x8co\x94g\xdc\xafPeQ\x9e\xa5.\x86\xc1\xdc\rbT\xb9B=\xdc\xb8RH\xc5\x0cJ\xfe\xde\xd5<E\xec\x98\xb2/I\x9c\xdc\xecFk\xc8>\xfed\xab\x06\xbdM\xc0\x0c\x00.\x00\x01\x00\x00\x15\xdb\x00\x9b\x000\x07\x02\x00\x00\x1c T\xa4\xb8]T\x9bo\xcdt!\x0

b'\x1e\xd5\x81\x80\x00\x01\x00\x1f\x00\x06\x00\x00\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x00\x0f\x00\x01\x00\x00\x08C\x00\t\x00\x14\x04emgw\xc0\x0c\xc0\x0c\x00.\x00\x01\x00\x00\x07+\x00\x9b\x00\x0f\x07\x02\x00\x00\x1c T\xa3f\xdeT\x9a\x1eNt!\x03irs\x03gov\x00w\xa0\xac?\x03+\x98\xe3\x19g\x90\xab\xfd\xc0\xf0{\xb1f\xbdp\xf7T6\xd9Lz\xce\xce\xed<\xcd\x91^<\x12A\xf0\xebaS/\x00\xe2\xca\xcd\xba\x92\x98\x93\x84\x02\x83\xbeY.\x881\x1d0\xbf%\xc9\xb9\xd7OE\xb5\xbd\xa9\x988L\xd4\xbb\x1a\xce\x0b\x1b\xd0g\x032$\r\\\tG\xa2\xf8\x05\x08m\xe4"\xf2\xe5\xe8\x88=\x13G\x85RG\xb61\xa0\xde+#\xa3KR\xde\xb0\xb3\xb3\xe9\xa8qDr\xb6\xd3\x0bK\x0c\xa0\xc0\x0c\x00.\x00\x01\x00\x00\x07+\x00\x9b\x00\x02\x07\x02\x00\x00\x1c T\xa3f\xdeT\x9a\x1eNt!\x03irs\x03gov\x00_\xf9\x04\x1c\xee\xd0\xa3J^`\xdcj_\xa4\x86M|\xb2n\x82\xf6]\x10\x83\x15\xef;\xfe\xe5\x9e\xebw\xaa\xf3\x01\x9d\x18\\\xe4\xb8z\xe6\xb4!\xd9\x01\xfd\xfbl\xf3\xe3Q\x88\xf3\x1e\xaf\x02\x13\xa5K\x02\x98\x03\x8d\x94\xfdde]f\x0c\xaf\x13\x9a\xd6\xd1\x8cH\\Wy!\x1d\x0c\x

# 968
b'n\x12\x81\x80\x00\x01\x00\x1b\x00\x06\x00\x14\x03irs\x03gov\x00\x00\xff\x00\x01\xc0\x0c\x00.\x00\x01\x00\x00\x0bo\x00\x97\x00+\x08\x02\x00\x00\x0e\x10T\xa5\x1d\x06T\x9b\xe2\x863\x9e\x03gov\x00*\x97\x1b\x92\x8e\xfcC\x06\xcf\x02\xb6 %t\xeb\xf2;X`\x0e\x8b\x07\x0fa\xc3\x0ea?\xd2o\xe4\x90&\x811\xe9\x86n\x06m\x08\x8e\xc4\xd4\xbf?\x0fS\xa0\xbd\x8bS\xa3\xc4\x94\xef\xa1\xc5\xd0[5p\xd37\x93\xbb)\x9f\x8a\x0b\x03r\xeb!c:\xf1G:\xd18\xe7\xd3\xddD\xe4\x04\'\x1e$\x91]\xf6\x81\xaaRYG\xcbc\xd3\x16\xab\x94\xc4\x07C\x8e\x8f\x8d\x04\xf6\x1ek\x17)\xe7\x80~T%\xd9\x0f^V@\xe6\x16\xc0\x0c\x00+\x00\x01\x00\x00\x0bo\x00$\x03v\x07\x02\x83\x9f\x8b\xf5\xd6\x00\xecOm.\xa7\x8c\x8e\xaf\xaf<\x9a\x00\xf9\x06\xdb\nG\x1f\x18u.\xd6+\x93\x08\xae\xc0\x0c\x00\x02\x00\x01\x00\x00\x0c\xff\x00\x06\x03ns1\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x0c\xff\x00\x06\x03ns3\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x0c\xff\x00\x06\x03ns4\xc0\x0c\xc0\x0c\x00\x02\x00\x01\x00\x00\x0c\xff\x00\x06\x03ns6\xc0\x0c\xc0\x0c\x00\x02\x00\x01\

KeyboardInterrupt: 

### Get attack keys of DDoS attacks containing only DNS traffic

In [ ]:
path_to_json = 'signatures/'
json_files = [pos_json for pos_json in os.listdir(path_to_json) if pos_json.endswith('.json')]

dns_keys=[]

for jf in json_files:
    with open('signatures/' + jf) as f:
        data=json.load(f)
    protocol = data.get("protocol")

    if protocol == "DNS":
        dns_keys.append(jf[:-5])

print("# of DNS DDoS attacks: ", len(dns_keys))

### Get AMI score and other stats per DNS DDoS Attack

In [ ]:
start = time.time()
most_important_features = []
AMI_values = {}
counter = 0
#iterate over all attack keys with DNS attacks
for attack_key in dns_keys:
    try:
        input = open('attack_pcaps/' + attack_key + '.pcap', 'rb')
        attack = dpkt.pcap.Reader(input)
        
        udp_packet = 0
        tcp_packet = 0
        dns_packet = 0
        other = 0
        total_packet = 0
        c = False
        ############### 
        #loop trough packets to get the number of packets in the attack
        #############
        for ts, buf in attack:
            eth = dpkt.ethernet.Ethernet(buf)
            total_packet += 1 
            if total_packet > 20000:
                print("continue")
                print("##########")
                c = True
                break
                
        if c:
            continue
            
        input.close()
        counter += 1
        print("# ", counter, "/", len(dns_keys))
        print("attackkey: ", attack_key)
        print("total # of packets: %s"  % (total_packet))

        #######################*dns*
        #initialize numpy arrays for all the to measure features
        ##############################
        ips_a = np.empty(total_packet)
        protocol_a = np.empty(total_packet)
        total_length_a = np.empty(total_packet)
        src_port_a = np.empty(total_packet)
        dst_port_a = np.empty(total_packet)
        udp_length_a = np.empty(total_packet)
        
        dns_opcode_a = np.empty(total_packet)
        dns_answerlength_a = np.empty(total_packet)
        dns_questionlength_a = np.empty(total_packet)
        dns_additional_recordlength_a = np.empty(total_packet)
        dns_RRlength_a = np.empty(total_packet)

        dns_flag_response_a = np.empty(total_packet)
        dns_flag_truncated_a = np.empty(total_packet)
        dns_flag_authorative_a = np.empty(total_packet)
        dns_flag_recursiond_a = np.empty(total_packet)
        dns_flag_recursiona_a = np.empty(total_packet)

        dns_reply_code_a = np.empty(total_packet)

        dns_answer_type_a = np.empty(total_packet)
        dns_answer_class_a = np.empty(total_packet)
        dns_answer_name_a = np.empty(total_packet)
        dns_answer_size_a = np.empty(total_packet)

        dns_question_name_a = np.empty(total_packet)
        dns_question_class_a = np.empty(total_packet)
        dns_question_type_a = np.empty(total_packet)
        
        labels_a = np.ones(total_packet)    
        
        ###############
        #loop trough packets and gather features
        #########
        input = open('attack_pcaps/' + attack_key + '.pcap', 'rb')
        attack = dpkt.pcap.Reader(input)
        i = 0
        for ts, buf in attack:
            eth = dpkt.ethernet.Ethernet(buf)
            pkt = scapy.layers.l2.Ether(buf)
            if pkt.haslayer('IP'):
                ip = pkt['IP']
                ips_a[i] = Utils.ip_to_uint32(ip.src)
                protocol_a[i] = ip.proto
                total_length_a[i] = ip.len
                if ip.proto == 6:
                    tcp_packet += 1
                    tcp = pkt['TCP']
                    dst_port_a[i] = tcp.dport
                    src_port_a[i] = tcp.sport
                elif ip.proto == 17:
                    udp_packet += 1
                    udp = pkt['UDP']
                    if pkt.haslayer(DNS):
                        dns_packet += 1
                        dns = pkt['DNS']
                        #dns = scapy.layers.dns.DNS(UDP.data)

                        dns_opcode_a[i] =  dns.opcode
                        dns_answerlength_a[i] = dns.ancount
                        dns_questionlength_a[i] = dns.qdcount
                        dns_additional_recordlength_a[i] = dns.arcount
                        dns_RRlength_a[i] = dns.nscount

                        dns_flag_response_a[i] = dns.qr
                        dns_flag_truncated_a[i] = dns.tc
                        dns_flag_authorative_a[i] = dns.aa #authorative answer
                        dns_flag_recursiond_a[i] = dns.rd
                        dns_flag_recursiona_a[i] = dns.ra

                        dns_reply_code_a[i] = dns.rcode

                        if (isinstance(dns.an, DNSRR)):
                            dns_answer_type_a[i] = dns.an.type
                            dns_answer_name_a[i] = int.from_bytes(dns.an.rrname, "little")
                            dns_answer_class_a[i] = dns.an.rclass
                            dns_answerlength_a[i] = dns.an.rdlen
                        else:
                            dns_answer_type_a[i] = -1
                            dns_answer_name_a[i] = -1
                            dns_answer_class_a[i] = -1
                            dns_answer_size_a[i] = -1

                        if (isinstance(dns.qd, DNSQR)):
                            dns_question_class_a[i] = dns.qd.qclass
                            dns_question_name_a[i] = int.from_bytes(dns.qd.qname, "little")
                            dns_question_type_a[i] = dns.qd.qtype
                        else:
                            dns_question_class_a[i] = -1
                            dns_question_name_a[i] = -1
                            dns_question_type_a[i] = -1



                        dst_port_a[i] = udp.dport
                        src_port_a[i] = udp.sport
                        udp_length_a[i] = udp.len
                else:
                    other += 1
                    dst_port_a[i] = 0
                    src_port_a[i] = 0
            else:
                other += 1

            i += 1
        
        ###############
        #make Numpy arrays with attack features and normal features together
        ################
        ips = np.append(ips_a, ips_n)
        protocol = np.append(protocol_a, protocol_n)
        total_length = np.append(total_length_a, total_length_n)
        src_port = np.append(src_port_a, src_port_n)
        dst_port = np.append(dst_port_a, dst_port_n)
        udp_length = np.append(udp_length_a, udp_length_n)
        
        dns_opcode = np.append(dns_opcode_a, dns_opcode_n)
        dns_answerlength = np.append(dns_answerlength_a, dns_answerlength_n)
        dns_questionlength = np.append(dns_questionlength_a, dns_questionlength_n)
        dns_RRlength = np.append(dns_RRlength_a, dns_RRlength_n)
        dns_additional_recordlength = np.append(dns_additional_recordlength_a, dns_additional_recordlength_n)
        
        dns_flag_response = np.append(dns_flag_response_a, dns_flag_response_n)
        dns_flag_truncated = np.append(dns_flag_truncated_a, dns_flag_truncated_n)
        dns_flag_authorative = np.append(dns_flag_authorative_a, dns_flag_authorative_n)
        dns_flag_recursiond = np.append(dns_flag_recursiond_a, dns_flag_recursiond_n)
        dns_flag_recursiona = np.append(dns_flag_recursiona_a, dns_flag_recursiona_n)

        dns_reply_code = np.append(dns_reply_code_a, dns_reply_code_n)

        dns_answer_type = np.append(dns_answer_type_a, dns_answer_type_n)
        dns_answer_class = np.append(dns_answer_class_a, dns_answer_class_n)
        dns_answer_name = np.append(dns_answer_name_a, dns_answer_name_n)
        dns_answer_size = np.append(dns_answer_size_a, dns_answer_size_n)

        dns_question_name = np.append(dns_question_name_a, dns_question_name_n)
        dns_question_class = np.append(dns_question_class_a, dns_question_class_n)
        dns_question_type = np.append(dns_question_type_a, dns_question_type_n)
        
        labels = np.append(labels_a, labels_n)

        features = [ips,protocol,total_length,src_port,dst_port,udp_length,dns_opcode,dns_answerlength,dns_questionlength,dns_flag_response,dns_flag_truncated,dns_flag_authorative,dns_flag_recursiond,dns_flag_recursiona,dns_reply_code,dns_answer_type,dns_answer_class,dns_answer_name,dns_answer_size,dns_question_name,dns_question_class,dns_question_type]

        
        ##########
        #Calculate adjusted mutual information score
        ############
        
        scores = []
        for x in features:
            score = adjusted_mutual_info_score(np.repeat(x,4), np.repeat(labels,4), "arithmetic")
            scores.append(score)
        AMI_values[attack_key] = scores
        ###########
        #Print all stats per attack
        #######

        print("# of UDP packets: %s" % (udp_packet))
        print("# of TCP packets: %s" % (tcp_packet))
        print("# of DNS packets: %s" % (dns_packet))
        print("# of other packets except for TCP or UDP: %s"  % (other))
        print("Features: ips,protocol,total_length,src_port,dst_port,udp_length,dns_opcode,dns_answerlength,dns_questionlength,dns_flag_response,dns_flag_truncated,dns_flag_authorative,dns_flag_recursiond,dns_flag_recursiona,dns_reply_code,dns_answer_type,dns_answer_class,dns_answer_name,dns_answer_size,dns_question_name,dns_question_class,dns_question_type")
        print("AMI scores: ", scores)
        
        max_index, max_value = max(enumerate(scores), key=operator.itemgetter(1))
        most_important_features.append(max_index)
        print("Most important feature: ", max_index)
        end = time.time()
        print(end - start)
        print("#####################################")
    except Exception as e:
        print("something went wrong here ", attack_key)
        exc_type, exc_obj, exc_tb = sys.exc_info()
        fname = os.path.split(exc_tb.tb_frame.f_code.co_filename)[1]
        print(exc_type, fname, exc_tb.tb_lineno)
        print(e)
print(end - start)

In [ ]:
with open('data.json', 'w') as json_file:
  json.dump(AMI_values, json_file)


### Analysis and Conclusions

In [ ]:
for i in range(0,22):
    print(i,most_important_features.count(i))

0 ips, <br/>
1 protocol, <br/>
2 total_length, <br/>
3 src_port, <br/>
4 dst_port, <br/>
5 udp_length, <br/>
6 dns_opcode, <br/>
7 dns_answerlength, <br/>
8 dns_questionlength, <br/>
9 dns_flag_response, <br/>
10 dns_flag_truncated, <br/>
11 dns_flag_authorative, <br/>
12 dns_flag_recursiond, <br/>
13 dns_flag_recursiona, <br/>
14 dns_reply_code, <br/>
15 dns_answer_type, <br/>
16 dns_answer_class, <br/>
17 dns_answer_name, <br/>
18 dns_answer_size, <br/>
19 dns_question_name, <br/>
20 dns_question_class, <br/>
21 dns_question_type <br/>